In [5]:
from sqlalchemy import create_engine, inspect
import subprocess
import pandas as pd
import geopandas as gpd
import psycopg2
from psycopg2 import sql
import plotly.express as px
import matplotlib.pyplot as plt
import time
import sys
import folium

In [2]:
# create a connection to the database
db_name = 'urbanmining'
db_user = 'postgres'
db_password = 'Tunacompany5694!'
db_host = 'localhost'
db_port = '5432'
engine = create_engine(f'postgresql://{db_user}:{db_password}@{db_host}:{db_port}/{db_name}')


In [6]:
gdf = gpd.read_file('../data/raw/landuse/landuse.gml')

In [8]:
gdf.description.unique()

array(['Railroad', 'Main road', 'Airport', 'Residential',
       'Retail trade, hotel and catering', 'Public institutions',
       'Socio-cultural facility', 'Industrial area and offices',
       'Dumping site', 'Car wreck site', 'Cemetery', 'Mining area',
       'Building site', 'Other semi built-up area',
       'Park and public garden', 'Sports ground (incl. car parks)',
       'Allotment garden', 'Area for daytrips', 'Holiday recreation',
       'Greenhouses', 'Other agricultural usage', 'Woodland',
       'Dry natural area', 'Wet natural area', 'Ijsselmeer of Markermeer',
       'Enclosed estuary', 'Rijn & Maas', 'Randmeer', 'Water reservoir',
       'Water with recreational usage',
       'Water where minerals are extracted',
       'Area for storing industrial water', 'Other inland water',
       'Waddenzee, Eems, Dollard', 'Oosterschelde', 'Westerschelde',
       'Noordzee', 'Foreign countries'], dtype=object)

In [3]:
from osgeo import ogr

# Path to your GML file
gml_file_path = '../data/raw/landuse/landuse.gml'

# Step 1: Open the GML file
gml_driver = ogr.GetDriverByName('GML')
gml_data_source = gml_driver.Open(gml_file_path, 0)  # 0 means read-only mode

if gml_data_source is None:
    print("Could not open GML file")
    exit()

# Step 2: Get the first layer
layer = gml_data_source.GetLayerByIndex(0)

if layer is None:
    print("No layer found in the GML file")
    exit()

print(f"Layer Name: {layer.GetName()}")
print(f"Number of features: {layer.GetFeatureCount()}")

# Step 3: Check geometries and properties for the first 10 features
feature_count = 0
geometry_count = 0
max_features = 10  # Limit to the first 10 features

for feature in layer:
    if feature_count >= max_features:
        break

    feature_count += 1
    geom = feature.GetGeometryRef()
    
    if geom is not None:
        geometry_count += 1
        print(f"Feature {feature_count}: Geometry Type: {geom.GetGeometryName()}")
    else:
        print(f"Feature {feature_count}: No geometry found")
    
    # Step 4: Inspect properties and handle duplicates
    properties = feature.items()  # Extract properties as a dictionary
    print(f"Feature {feature_count}: Properties (Raw): {properties}")
    
    # Handle duplicates if necessary
    seen_fields = set()
    cleaned_properties = {}
    for key, value in properties.items():
        if key in seen_fields:
            print(f"Duplicate field '{key}' detected. Handling...")
            # Optionally, rename the duplicate or ignore it (e.g., use a suffix or only keep the first occurrence)
            cleaned_properties[f"{key}_duplicate"] = value
        else:
            cleaned_properties[key] = value
            seen_fields.add(key)
    
    print(f"Feature {feature_count}: Cleaned Properties: {cleaned_properties}")

print(f"\nTotal features processed: {feature_count}")
print(f"Total features with geometries: {geometry_count}")

# Close the data source
gml_data_source = None



Layer Name: ExistingLandUseObject
Number of features: 171543
Feature 1: Geometry Type: MULTIPOLYGON
Feature 1: Properties (Raw): {'gml_id': 'BBG2017_1', 'description': 'Railroad', 'name': '4_1_2', 'localId': 'BBG2017_1', 'namespace': 'NL.CBS.LU.ExistingLandUseObject', 'beginLifespanVersion': None, 'hilucsPresence': None, 'specificPresence': None, 'observationDate': '2017-07-31', 'validFrom': '2017-04-15', 'validTo': '2017-09-15'}
Feature 1: Cleaned Properties: {'gml_id': 'BBG2017_1', 'description': 'Railroad', 'name': '4_1_2', 'localId': 'BBG2017_1', 'namespace': 'NL.CBS.LU.ExistingLandUseObject', 'beginLifespanVersion': None, 'hilucsPresence': None, 'specificPresence': None, 'observationDate': '2017-07-31', 'validFrom': '2017-04-15', 'validTo': '2017-09-15'}
Feature 2: Geometry Type: MULTIPOLYGON
Feature 2: Properties (Raw): {'gml_id': 'BBG2017_2', 'description': 'Railroad', 'name': '4_1_2', 'localId': 'BBG2017_2', 'namespace': 'NL.CBS.LU.ExistingLandUseObject', 'beginLifespanVersion'

Warning 1: Field with same name (description) already exists in (ExistingLandUseObject). Skipping newer ones
Warning 1: Field with same name (name) already exists in (ExistingLandUseObject). Skipping newer ones


In [5]:
query = ''' 
SELECT neighborhood_code, geom
FROM housing_nl
WHERE
    municipality = 'Amsterdam'
    AND neighborhood_code !~ '^BU\d{8}$'
'''
gdf = gpd.read_postgis(query, engine, geom_col='geom')

In [9]:
# plot gdf on folium
m = folium.Map(location=[52.3702, 4.8952], zoom_start=12)
folium.GeoJson(gdf.sample(10000)).add_to(m)
m